<a href="https://colab.research.google.com/github/sahabajalam/amazon_fine_food_review/blob/main/My_AFFR.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [61]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [62]:
import sqlite3
import pandas as pd
import numpy as np
import nltk
import string
import sqlalchemy
from sqlalchemy import create_engine
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics import confusion_matrix
from sklearn import metrics
from sklearn.metrics import roc_curve, auc
from nltk.stem.porter import PorterStemmer

import re
# Tutorial about Python regular expressions: https://pymotw.com/2/re/
import string
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer

from gensim.models import Word2Vec
from gensim.models import KeyedVectors
import pickle

from tqdm import tqdm
import os

In [63]:
from sqlalchemy import create_engine
my_conn=create_engine("sqlite:////content/drive/MyDrive/Colab Notebooks/Apllied_roots/AFFR/database.sqlite")

In [64]:
conn=sqlite3.connect('database.sqlite')


In [65]:
d_tab=my_conn.execute('''SELECT name FROM sqlite_master''')
for row in d_tab:
  print(row)

('Reviews',)


In [66]:
filtered_data = pd.read_sql_query(""" SELECT * FROM Reviews WHERE Score != 3 LIMIT 50000""", my_conn) 


In [67]:
filtered_data.head(5)

Id  ...                                               Text
0   1  ...  I have bought several of the Vitality canned d...
1   2  ...  Product arrived labeled as Jumbo Salted Peanut...
2   3  ...  This is a confection that has been around a fe...
3   4  ...  If you are looking for the secret ingredient i...
4   5  ...  Great taffy at a great price.  There was a wid...

[5 rows x 10 columns]

In [68]:
d_tab=my_conn.execute(""" SELECT * FROM Reviews WHERE Score != 3 LIMIT 50000""")
for info in d_tab:
  print (info)

Streaming output truncated to the last 5000 lines.
(3053, 'B0000E65W9', 'A1GJ37VZOZ6S1W', 'S. Jettlund "mamaknows2much"', 0, 0, 5, 1308700800, 'A Staple in my house', 'I use these to keep my finicky toddler\'s protein levels up. What\'s great, is that they\'re delicious just about any way you can imagine cooking a s ... (389 characters truncated) ... ally use about a half a pound, and frozen would work fine, just put it in a minute earlier). Stir until the spinach is cooked, and then serve! Enjoy!')
(3054, 'B003V1HH42', 'AMCHLVS2PM9X6', 'Katie Valin', 0, 0, 5, 1348185600, 'Best Coffee Ever...', "Having recently purchased a single cup coffee maker, we discovered Green Mountain and their delicious varieties of coffee.  I love the Island Coconut ... (164 characters truncated) ... e through.  Try it with a little Chocolate Coffee Mate Creamer and you'll swear you were having a decadent treat straight from the Islands...  YUM!!!")
(3055, 'B003V1HH42', 'A22CMAQIXN4TW3', 'Bright Eyes', 0, 0, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
(16529, 'B003VZCZ0O', 'AJCK6OKNWGIYG', 'Mike K', 1, 1, 5, 1295222400, 'Love this cereal', "I love cereal in general and Lucky Charms is up there as one of my favorites. I like my cereals a little sweet and Lucky Charms is just that. It's no ... (133 characters truncated) ... his cereal doesn't get that soggy after being in the milk for a little while. The taste is great and I can't get tired of it like some other cereals.")
(16530, 'B003VZCZ0O', 'A1BTV36SOS1FT3', 'Richard A. Knight "Rick"', 0, 0, 5, 1322265600, 'How can you go wrong?', 'Great Food! Great Price with subscribe and save saved 15% of the list price.  3 boxes go fast but they are good.')
(16531, 'B003VZCZ0O', 'A2O6HZ2B9YSRXR', 'Indiana Customer', 0, 0, 5, 1319068800, 'my favorite cereal at a great price with subscribe and save.', "I am set on my favorite cereal now for as long as Amazon offers the subscribe and save deal, can't beat that.  I used to not eat Lucky Charms tha

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
(32204, 'B000FA15RW', 'A3TD6UP32OFJR3', 'Jeremy Lee', 3, 7, 1, 1260662400, 'gross cookies', "When I eat junk food, I'd like to enjoy it, the guilty pleasure it is.<br /><br />These cookies are neither healthy or tasty.  Stick to Chewy Chocolate Chip cookies.")
(32205, 'B000FA15RW', 'A4QCYNKAT2UN', 'jason h. "jason h"', 2, 7, 1, 1256601600, 'EHKKKKKKKKKKKKKKK', "tastes pretty crappy. it's like raw cookies.<br /><br />it's not even like a cookie. it's a squishy thing in a cookie shape")
(32206, 'B000FA15RW', 'A5SKCSDE1O8T8', 'J. Taylor', 1, 6, 2, 1254182400, 'Bad flavor combination', 'I purchased these thinking they would just be ordinary oatmeal raisin cookies. Wrong! I like chocolate chip and I like oatmeal raisin but these combination cookies just don\'t work well together. I wish I had read the item listing more carefully. Even my kids said "Blech!".')
(32207, 'B000FA15RW', 'A2QPLZN1CXNXAE', 'Ropo', 1, 7, 1, 1279152000, "Pathetic coo

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
(44425, 'B000LDQWHG', 'A48ER82TCYAPT', 'Rusty Shackleford "R"', 1, 1, 4, 1223769600, 'Made in China', "I have been having good luck with these with my two lab mutts.  I load a couple into a Busy Buddy for each of them and they love them.  I think it he ... (191 characters truncated) ... r the pet food recall, lead paint in toys, milk debacle, etc..).  Hopefully I can figure out a recipe to copy these things because they do work well.")
(44426, 'B000LDQWHG', 'A2IHM077DKGS6K', 'Francine R., Rose "Francine"', 0, 0, 5, 1343088000, 'Treats for Chewers!', "Jack is a 3.5 year old papillon.  He enjoys chewing.  I found this product years ago and he still enjoys it today.  It's pet friendly and entertains him for the time he takes to chew.  Recommended for any canine that enjoys exercising his jaws!")
(44427, 'B000LDQWHG', 'AJQWUGRNRKM9K', 'Mary', 0, 0, 5, 1337558400, 'Kiesha loves these!!', 'My dog loves this toy.  She can go thru a few of the

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Partition review where rating is less tahn 3

In [69]:
def partition(x):
    if x < 3:
        return 0
    return 1
    

In [70]:
actualScore = filtered_data['Score']
positiveNegative = actualScore.map(partition) 
filtered_data['Score'] = positiveNegative
print("Number of data points in our data", filtered_data.shape)
filtered_data.head(3)

Number of data points in our data (50000, 10)


Id  ...                                               Text
0   1  ...  I have bought several of the Vitality canned d...
1   2  ...  Product arrived labeled as Jumbo Salted Peanut...
2   3  ...  This is a confection that has been around a fe...

[3 rows x 10 columns]

In [71]:
display = pd.read_sql_query("""
SELECT UserId, ProductId, ProfileName, Time, Score, Text, COUNT(*)
FROM Reviews
GROUP BY UserId
HAVING COUNT(*)>1
""", my_conn)

In [72]:
print(display.shape)
display.head()

(80668, 7)


UserId  ... COUNT(*)
0  #oc-R115TNMSPFT9I7  ...        2
1  #oc-R11D9D7SHXIJB9  ...        3
2  #oc-R11DNU2NBKQ23Z  ...        2
3  #oc-R11O5J5ZVQE25C  ...        3
4  #oc-R12KPBODL2B5ZD  ...        2

[5 rows x 7 columns]

In [73]:
display[display['UserId']=='AZY10LLTJ71NX']

UserId  ... COUNT(*)
80638  AZY10LLTJ71NX  ...        5

[1 rows x 7 columns]

In [74]:
display['COUNT(*)'].sum()

393063

In [75]:
sorted_data=filtered_data.sort_values('ProductId', axis=0, ascending=True, inplace=False, kind='quicksort', na_position='last')

In [76]:
final=sorted_data.drop_duplicates(subset={"UserId","ProfileName","Time","Text"}, keep='first', inplace=False)
final.shape

(46072, 10)

In [77]:
(final['Id'].size*1.0)/(filtered_data['Id'].size*1.0)*100

92.144

In [78]:
display= pd.read_sql_query("""
SELECT *
FROM Reviews
WHERE Score != 3 AND Id=44737 OR Id=64422
ORDER BY ProductID
""", my_conn)

display.head()

Id  ...                                               Text
0  64422  ...  My son loves spaghetti so I didn't hesitate or...
1  44737  ...  It was almost a 'love at first bite' - the per...

[2 rows x 10 columns]

In [79]:
final=final[final.HelpfulnessNumerator<=final.HelpfulnessDenominator]

In [80]:
print(final.shape)
final['Score'].value_counts()

(46071, 10)


1    38479
0     7592
Name: Score, dtype: int64

**Text Preprocessing**

In [81]:
sorted_data=filtered_data.sort_values('ProductId', axis=0, ascending=True, inplace=False, kind='quicksort', na_position='last')

In [82]:
final=sorted_data.drop_duplicates(subset={"UserId","ProfileName","Time","Text"}, keep='first', inplace=False)
final.shape

(46072, 10)

In [83]:
(final['Id'].size*1.0)/(filtered_data['Id'].size*1.0)*100

92.144

In [84]:
display= pd.read_sql_query("""
SELECT *
FROM Reviews
WHERE Score != 3 AND Id=44737 OR Id=64422
ORDER BY ProductID
""", my_conn)

display.head()

Id  ...                                               Text
0  64422  ...  My son loves spaghetti so I didn't hesitate or...
1  44737  ...  It was almost a 'love at first bite' - the per...

[2 rows x 10 columns]

In [85]:
final=final[final.HelpfulnessNumerator<=final.HelpfulnessDenominator]

In [86]:
print(final.shape)


(46071, 10)


In [87]:
# printing some random reviews
sent_0 = final['Text'].values[0]
print(sent_0)
print("="*50)

sent_10 = final['Text'].values[10]
print(sent_10)
print("="*50)

sent_100 = final['Text'].values[100]
print(sent_100)
print("="*50)

sent_498 = final['Text'].values[498]
print(sent_498)
print("="*50)

My dogs loves this chicken but its a product from China, so we wont be buying it anymore.  Its very hard to find any chicken products made in the USA but they are out there, but this one isnt.  Its too bad too because its a good product but I wont take any chances till they know what is going on with the china imports.
I've been trying to find the individual-pack option (at the affordable price) for months now. I love having the ability to know exactly how much creamer I'm using by counting the individual packets. (This product isn't available in my grocery store-- just by the coffee dispensers at local convenience stores.) They're perfect for keeping at my desk at work~~I don't have to use the community fridge, and it doesn't lump up in my coffee like the powdered versions do. It's a little less convenient at home, though, where I'm accustomed to using my refrigerated bottled versions~~opening the little packets one at a time at 5 am can get annoying--but then again, I know exactly ho

In [88]:
# remove urls from text python: https://stackoverflow.com/a/40823105/4084039
sent_0 = re.sub(r"http\S+", "", sent_0)
sent_10 = re.sub(r"http\S+", "", sent_10)
sent_100 = re.sub(r"http\S+", "", sent_100)
sent_498 = re.sub(r"http\S+", "", sent_498)

print(sent_0)
print(sent_10)
print(sent_100)
print(sent_498)

My dogs loves this chicken but its a product from China, so we wont be buying it anymore.  Its very hard to find any chicken products made in the USA but they are out there, but this one isnt.  Its too bad too because its a good product but I wont take any chances till they know what is going on with the china imports.
I've been trying to find the individual-pack option (at the affordable price) for months now. I love having the ability to know exactly how much creamer I'm using by counting the individual packets. (This product isn't available in my grocery store-- just by the coffee dispensers at local convenience stores.) They're perfect for keeping at my desk at work~~I don't have to use the community fridge, and it doesn't lump up in my coffee like the powdered versions do. It's a little less convenient at home, though, where I'm accustomed to using my refrigerated bottled versions~~opening the little packets one at a time at 5 am can get annoying--but then again, I know exactly ho

In [89]:
# https://stackoverflow.com/questions/16206380/python-beautifulsoup-how-to-remove-all-tags-from-an-element
from bs4 import BeautifulSoup

soup = BeautifulSoup(sent_0, 'lxml')
text = soup.get_text()
print(text)
print("="*50)

soup = BeautifulSoup(sent_10, 'lxml')
text = soup.get_text()
print(text)
print("="*50)

soup = BeautifulSoup(sent_100, 'lxml')
text = soup.get_text()
print(text)
print("="*50)

soup = BeautifulSoup(sent_498, 'lxml')
text = soup.get_text()
print(text)

My dogs loves this chicken but its a product from China, so we wont be buying it anymore.  Its very hard to find any chicken products made in the USA but they are out there, but this one isnt.  Its too bad too because its a good product but I wont take any chances till they know what is going on with the china imports.
I've been trying to find the individual-pack option (at the affordable price) for months now. I love having the ability to know exactly how much creamer I'm using by counting the individual packets. (This product isn't available in my grocery store-- just by the coffee dispensers at local convenience stores.) They're perfect for keeping at my desk at work~~I don't have to use the community fridge, and it doesn't lump up in my coffee like the powdered versions do. It's a little less convenient at home, though, where I'm accustomed to using my refrigerated bottled versions~~opening the little packets one at a time at 5 am can get annoying--but then again, I know exactly ho

In [90]:
# https://stackoverflow.com/a/47091490/4084039
import re

def decontracted(phrase):
    # specific
    phrase = re.sub(r"won't", "will not", phrase)
    phrase = re.sub(r"can\'t", "can not", phrase)

    # general
    phrase = re.sub(r"n\'t", " not", phrase)
    phrase = re.sub(r"\'re", " are", phrase)
    phrase = re.sub(r"\'s", " is", phrase)
    phrase = re.sub(r"\'d", " would", phrase)
    phrase = re.sub(r"\'ll", " will", phrase)
    phrase = re.sub(r"\'t", " not", phrase)
    phrase = re.sub(r"\'ve", " have", phrase)
    phrase = re.sub(r"\'m", " am", phrase)
    return phrase

In [91]:
sent_100 = decontracted(sent_100)
print(sent_100)
print("="*50)

Just an FYI to other customers: This item is for the Beef and Ocean Fish formula which is in a RED bag. In my haste, I purchased this thinking it was a the 15lb version of the Chicken and Rice formula. Woops! So I went and bought the 15lb bag of Chicken and Rice and mix the Beef and Fish in so it did not wreak havoc on my pup is digestive system.<br /><br />I can say that after we started feeding this to my pup, she starting having stinky farts and had never had them before. Also, Roshan is right about the fish breath! Ick.<br /><br />Overall, my dog has no issues with this formula, it is just stinky so I will stick to Chicken and Rice after this bag is done.


In [92]:
#remove words with numbers python: https://stackoverflow.com/a/18082370/4084039
sent_0 = re.sub("\S*\d\S*", "", sent_0).strip()
print(sent_0)

My dogs loves this chicken but its a product from China, so we wont be buying it anymore.  Its very hard to find any chicken products made in the USA but they are out there, but this one isnt.  Its too bad too because its a good product but I wont take any chances till they know what is going on with the china imports.


In [93]:
#remove spacial character: https://stackoverflow.com/a/5843547/4084039
sent_100 = re.sub('[^A-Za-z0-9]+', ' ', sent_100)
print(sent_100)

Just an FYI to other customers This item is for the Beef and Ocean Fish formula which is in a RED bag In my haste I purchased this thinking it was a the 15lb version of the Chicken and Rice formula Woops So I went and bought the 15lb bag of Chicken and Rice and mix the Beef and Fish in so it did not wreak havoc on my pup is digestive system br br I can say that after we started feeding this to my pup she starting having stinky farts and had never had them before Also Roshan is right about the fish breath Ick br br Overall my dog has no issues with this formula it is just stinky so I will stick to Chicken and Rice after this bag is done 


In [94]:
# https://gist.github.com/sebleier/554280
# we are removing the words from the stop words list: 'no', 'nor', 'not'
# <br /><br /> ==> after the above steps, we are getting "br br"
# we are including them into stop words list
# instead of <br /> if we have <br/> these tags would have revmoved in the 1st step

stopwords= set(['br', 'the', 'i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've",\
            "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', \
            'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their',\
            'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', \
            'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', \
            'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', \
            'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after',\
            'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further',\
            'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more',\
            'most', 'other', 'some', 'such', 'only', 'own', 'same', 'so', 'than', 'too', 'very', \
            's', 't', 'can', 'will', 'just', 'don', "don't", 'should', "should've", 'now', 'd', 'll', 'm', 'o', 're', \
            've', 'y', 'ain', 'aren', "aren't", 'couldn', "couldn't", 'didn', "didn't", 'doesn', "doesn't", 'hadn',\
            "hadn't", 'hasn', "hasn't", 'haven', "haven't", 'isn', "isn't", 'ma', 'mightn', "mightn't", 'mustn',\
            "mustn't", 'needn', "needn't", 'shan', "shan't", 'shouldn', "shouldn't", 'wasn', "wasn't", 'weren', "weren't", \
            'won', "won't", 'wouldn', "wouldn't"])

In [95]:
# Combining all the above stundents 
from tqdm import tqdm
preprocessed_reviews = []
# tqdm is for printing the status bar
for sentance in tqdm(final['Text'].values):
    sentance = re.sub(r"http\S+", "", sentance)
    sentance = BeautifulSoup(sentance, 'lxml').get_text()
    sentance = decontracted(sentance)
    sentance = re.sub("\S*\d\S*", "", sentance).strip()
    sentance = re.sub('[^A-Za-z]+', ' ', sentance)
    # https://gist.github.com/sebleier/554280
    sentance = ' '.join(e.lower() for e in sentance.split() if e.lower() not in stopwords)
    preprocessed_reviews.append(sentance.strip())

100%|██████████| 46071/46071 [00:18<00:00, 2544.55it/s]


In [96]:
preprocessed_reviews[470]

'bought amazon not seller depicted currently plant looked great arrival died days despite trying hard following instructions wonder shipping box depriving light etc days causes damage'

In [97]:
#BoW
count_vect = CountVectorizer() #in scikit-learn
count_vect.fit(preprocessed_reviews)
print("some feature names ", count_vect.get_feature_names()[:10])
print('='*50)

final_counts = count_vect.transform(preprocessed_reviews)
print("the type of count vectorizer ",type(final_counts))
print("the shape of out text BOW vectorizer ",final_counts.get_shape())
print("the number of unique words ", final_counts.get_shape()[1])

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


some feature names  ['aa', 'aaa', 'aaaa', 'aaaaa', 'aaaaaaaaaaaa', 'aaaaaaaaaaaaaaa', 'aaaaaaahhhhhh', 'aaaaaawwwwwwwwww', 'aaaaah', 'aaaand']
the type of count vectorizer  <class 'scipy.sparse.csr.csr_matrix'>
the shape of out text BOW vectorizer  (46071, 39364)
the number of unique words  39364


In [98]:
#bi-gram, tri-gram and n-gram

#removing stop words like "not" should be avoided before building n-grams
# count_vect = CountVectorizer(ngram_range=(1,2))
# please do read the CountVectorizer documentation http://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.CountVectorizer.html
# you can choose these numebrs min_df=10, max_features=5000, of your choice
count_vect = CountVectorizer(ngram_range=(1,2), min_df=10, max_features=5000)
final_bigram_counts = count_vect.fit_transform(preprocessed_reviews)
print("the type of count vectorizer ",type(final_bigram_counts))
print("the shape of out text BOW vectorizer ",final_bigram_counts.get_shape())
print("the number of unique words including both unigrams and bigrams ", final_bigram_counts.get_shape()[1])

the type of count vectorizer  <class 'scipy.sparse.csr.csr_matrix'>
the shape of out text BOW vectorizer  (46071, 5000)
the number of unique words including both unigrams and bigrams  5000


In [99]:
tf_idf_vect = TfidfVectorizer(ngram_range=(1,2), min_df=10)
tf_idf_vect.fit(preprocessed_reviews)
print("some sample features(unique words in the corpus)",tf_idf_vect.get_feature_names()[0:10])
print('='*50)

final_tf_idf = tf_idf_vect.transform(preprocessed_reviews)
print("the type of count vectorizer ",type(final_tf_idf))
print("the shape of out text TFIDF vectorizer ",final_tf_idf.get_shape())
print("the number of unique words including both unigrams and bigrams ", final_tf_idf.get_shape()[1])

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


some sample features(unique words in the corpus) ['ability', 'able', 'able buy', 'able chew', 'able drink', 'able eat', 'able enjoy', 'able feed', 'able figure', 'able find']
the type of count vectorizer  <class 'scipy.sparse.csr.csr_matrix'>
the shape of out text TFIDF vectorizer  (46071, 27311)
the number of unique words including both unigrams and bigrams  27311


In [100]:
# Train your own Word2Vec model using your own text corpus
i=0
list_of_sentance=[]
for sentance in preprocessed_reviews:
    list_of_sentance.append(sentance.split())

In [101]:
# Using Google News Word2Vectors

# in this project we are using a pretrained model by google
# its 3.3G file, once you load this into your memory 
# it occupies ~9Gb, so please do this step only if you have >12G of ram
# we will provide a pickle file wich contains a dict , 
# and it contains all our courpus words as keys and  model[word] as values
# To use this code-snippet, download "GoogleNews-vectors-negative300.bin" 
# from https://drive.google.com/file/d/0B7XkCwpI5KDYNlNUTTlSS21pQmM/edit
# it's 1.9GB in size.


# http://kavita-ganesan.com/gensim-word2vec-tutorial-starter-code/#.W17SRFAzZPY
# you can comment this whole cell
# or change these varible according to your need

is_your_ram_gt_16g=False
want_to_use_google_w2v = False
want_to_train_w2v = True

if want_to_train_w2v:
    # min_count = 5 considers only words that occured atleast 5 times
    w2v_model=Word2Vec(list_of_sentance,min_count=5,size=50, workers=4)
    print(w2v_model.wv.most_similar('great'))
    print('='*50)
    print(w2v_model.wv.most_similar('worst'))
    
elif want_to_use_google_w2v and is_your_ram_gt_16g:
    if os.path.isfile('GoogleNews-vectors-negative300.bin'):
        w2v_model=KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin', binary=True)
        print(w2v_model.wv.most_similar('great'))
        print(w2v_model.wv.most_similar('worst'))
    else:
        print("you don't have gogole's word2vec file, keep want_to_train_w2v = True, to train your own w2v ")

[('awesome', 0.8400673866271973), ('fantastic', 0.8212202787399292), ('terrific', 0.7988319993019104), ('good', 0.7987897396087646), ('excellent', 0.7951616048812866), ('wonderful', 0.7769986987113953), ('amazing', 0.77064049243927), ('perfect', 0.7432766556739807), ('fabulous', 0.6940610408782959), ('perky', 0.6748993396759033)]
[('best', 0.7060062885284424), ('nastiest', 0.6970707774162292), ('greatest', 0.6916804909706116), ('softest', 0.6869434714317322), ('awful', 0.6683713793754578), ('tastiest', 0.6617099046707153), ('ive', 0.6504926085472107), ('experienced', 0.6449517011642456), ('horrible', 0.6282671689987183), ('closest', 0.6219003200531006)]


In [102]:
w2v_words = list(w2v_model.wv.vocab)
print("number of words that occured minimum 5 times ",len(w2v_words))
print("sample words ", w2v_words[0:50])

number of words that occured minimum 5 times  12798
sample words  ['dogs', 'loves', 'chicken', 'product', 'china', 'wont', 'buying', 'anymore', 'hard', 'find', 'products', 'made', 'usa', 'one', 'isnt', 'bad', 'good', 'take', 'chances', 'till', 'know', 'going', 'imports', 'love', 'saw', 'pet', 'store', 'tag', 'attached', 'regarding', 'satisfied', 'safe', 'available', 'victor', 'traps', 'unreal', 'course', 'total', 'fly', 'pretty', 'stinky', 'right', 'nearby', 'used', 'bait', 'seasons', 'ca', 'not', 'beat', 'great']


In [103]:
# average Word2Vec
# compute average word2vec for each review.
sent_vectors = []; # the avg-w2v for each sentence/review is stored in this list
for sent in tqdm(list_of_sentance): # for each review/sentence
    sent_vec = np.zeros(50) # as word vectors are of zero length 50, you might need to change this to 300 if you use google's w2v
    cnt_words =0; # num of words with a valid vector in the sentence/review
    for word in sent: # for each word in a review/sentence
        if word in w2v_words:
            vec = w2v_model.wv[word]
            sent_vec += vec
            cnt_words += 1
    if cnt_words != 0:
        sent_vec /= cnt_words
    sent_vectors.append(sent_vec)
print(len(sent_vectors))
print(len(sent_vectors[0]))

100%|██████████| 46071/46071 [02:03<00:00, 373.08it/s]

46071
50


In [104]:
# S = ["abc def pqr", "def def def abc", "pqr pqr def"]
model = TfidfVectorizer()
model.fit(preprocessed_reviews)
# we are converting a dictionary with word as a key, and the idf as a value
dictionary = dict(zip(model.get_feature_names(), list(model.idf_)))

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [105]:
# TF-IDF weighted Word2Vec
tfidf_feat = model.get_feature_names() # tfidf words/col-names
# final_tf_idf is the sparse matrix with row= sentence, col=word and cell_val = tfidf

tfidf_sent_vectors = []; # the tfidf-w2v for each sentence/review is stored in this list
row=0;
for sent in tqdm(list_of_sentance): # for each review/sentence 
    sent_vec = np.zeros(50) # as word vectors are of zero length
    weight_sum =0; # num of words with a valid vector in the sentence/review
    for word in sent: # for each word in a review/sentence
        if word in w2v_words and word in tfidf_feat:
            vec = w2v_model.wv[word]
#             tf_idf = tf_idf_matrix[row, tfidf_feat.index(word)]
            # to reduce the computation we are 
            # dictionary[word] = idf value of word in whole courpus
            # sent.count(word) = tf valeus of word in this review
            tf_idf = dictionary[word]*(sent.count(word)/len(sent))
            sent_vec += (vec * tf_idf)
            weight_sum += tf_idf
    if weight_sum != 0:
        sent_vec /= weight_sum
    tfidf_sent_vectors.append(sent_vec)
    row += 1

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
100%|██████████| 46071/46071 [24:42<00:00, 31.09it/s]
